In [2]:
%plot -f svg

warning('off'); format compact;

graphics_toolkit("gnuplot");

set(0, "defaultfigurecolor", "none");
set(0, "defaultaxescolor",   "none");
set(0, "defaultfigureinverthardcopy", "off");

set(0, 'defaultaxesfontsize', 16);
set(0, 'defaulttextfontsize', 16);
set(0, 'defaultaxeslinewidth', 2);
set(0, 'defaultlinelinewidth', 4);

Tento markdown blok obsahuje definici Latexové makro `\Aop` pro MKP operátor sestavení globálních matic.
$\newcommand{\Aop}{\mathop{\vphantom{\sum}\vphantom{\rule{0pt}{2.5ex}}\smash{\lower{1.0ex}{\text{{\huge A}}}}}}$
$\newcommand{\Aop}{\displaystyle\mathop{\Large\mathrm{A}}\limits}$


## Disclaimer: jedná se o didaktický kód, ne produkční
- Zvolen jednoduchý programovací jazyk GNU Octave.
- Cílem je vysvětlit algoritmy na jednoduché implementaci.
- Bez snahy o solidní softwarový design a optimalizovaný kód.
- Chybí řádné ošetření chybových stavů a vyjímek.

## Jak s kódem pracovat?
- Buňky s kódem jsou "živé" a lze je volně editovat a kód provádět. A to tak, že umístíme kurzor do buňky a stiskneme `Shift+Enter`.
- Po provedení kódu zůstávají definované proměnné v paměti a původní hodnoty se přepíší.
- Na následující slide se přesouváme `mezerníkem`.
- V duchu *learning by doing* principu doporučuji paralelně s prezentací tvořit vlastní soubor s kódem.

## Řešení 2D úlohy lineární elasticity pomocí MKP
Vyjdeme ze slabé formulace (bez objemových sil):
$$
\int_{\Omega}\delta\boldsymbol{\varepsilon}:\mathcal{D}:\boldsymbol{\varepsilon}\,\text{d}V-\int_{\Gamma_{\text{N}}}\delta\boldsymbol{u}\cdot\bar{\boldsymbol{t}}\,\text{d}S=0
$$
a její MKP diskretizace:
$$
\delta\mathbf{u}^{\mathsf{T}}
\left\{ \left[\Aop_{el=1}^{n_{\text{el}}}\int_{\Omega_{el}}\mathbf{B}^{\mathsf{T}}\mathbf{D}\mathbf{B}\,\text{d}V_{el}\right]\mathbf{u}-\Aop_{el=1}^{n_{\text{el}}}\left[\int_{\Gamma_{\text{N}}^{e}}\mathbf{N}^{\mathsf{T}}\bar{\mathbf{t}}\,\text{d}S_{el}\right]\right\} =0
$$
která vede na lineární systém algebraický rovnic:
$$
\mathbf{K}\mathbf{u}-\mathbf{f}=\mathbf{0}
$$

Pro sestavení matice tuhosti a vektoru pravé strany:
$$
\mathbf{K}= 
\Aop_{el=1}^{n_\text{en}}
\sum_{g}\mathbf{B}_{g}^{\mathsf{T}}\mathbf{D}\mathbf{B}_{g}w_{g}\left\Vert J_{g}\right\Vert ,\qquad
\mathbf{f}=
\Aop_{el=1}^{n_\text{en}}
\sum_{g}\mathbf{N}^{\mathsf{T}}\bar{\mathbf{t}}_{g}w_{g}\left\Vert J_{g}^{\text{s}}\right\Vert 
$$
budeme potřebovat:
1. Oblast řešení a její diskretizace
2. Okrajové podmínky
3. Sestavení globání matice a vektoru
4. Gaussova inetgrace
5. Matice tvarových funkcí $\mathbf{N}$
6. Operátorová matice $\mathbf{B}$
7. Matice materiálové tuhosti $\mathbf{D}$
8. Řešení
9. Post-processing

## 1. Oblast řešení a její diskretizace

<table><tr>
<td style="width: 15%;">
    
![](assets/2D_bar_with_quads.svg)

</td>
<td style="width: 85%;">

Pro definovanou geometrii potřebujeme vytvořit výpočtovou síť. Síť v našém kódu budeme reprezentovat dvěma dvourozměrnými poli: polem souřadnic uzlů `X` a polem konektivity elementů `IEN`. Tyto pole můžeme pro jednoduché oblasti vytvořit ručně, ale pro složitější geometrie je užitečné použít tzv. síťovač, např. [Gmsh](https://gmsh.info).
    
<div class="llm-prompt">
<strong>LLM Prompt:</strong> Vytvoř mi vstupní soubor pro Gmsh `bar.geo`, pro 2D obdélník o délce L = 1 m a šířce b = sqrt(A) m, kde průřez A = 0.1 m^2. Počátek kartézských souřadnic zvol v levém horním rohu. Souřadnice b míří ve směru +x a L ve směru -y. Obdélník vysíťuj třemi lineárními quad elementy ve směru y. Normály quad elementů musí mířit ve směru +z, tj. curve loop číslování musí být proti směru hodinových ručiček (CCW) podle pravidla pravé ruky.
</div>
</td>
</tr></table>

### Souřadnice uzlových bodů

In [3]:
nsd = 2; % Number of Spatial Dimensions
run("assets/bar.m"); % read msh data structure exported from gmsh
X = msh.POS(:, 1:nsd)'




X =
        0        0   0.3162   0.3162        0        0   0.3162   0.3162
        0  -1.0000  -1.0000        0  -0.3333  -0.6667  -0.6667  -0.3333



### Pole konektivity


In [4]:
nen = 4; % Number of Element Nodes
IEN = msh.QUADS(:, 1:nen)'



IEN =
   1   5   6
   5   6   2
   8   7   3
   4   8   7



## 2. Okrajové podmínky

### Dirichletovy okrajové podmínky
2D pole `DBC`

In [5]:
DBC = [1 1 0.0   % at node 1 displacement X set to 0.0
       1 2 0.0   % at node 1 displacement Y set to 0.0
       4 2 0.0]; % at node 4 displacement Y set to 0.0

<div class="homework">
<strong>Úkol:</strong> Zkus změnit okrajovou podmínku tak, že prut nebude namáhán na tah, ale na smyk.
</div>

<table><tr>
<td style="width: 15%;">
    
![](assets/2D_bar_with_quads.svg)

</td>
<td style="width: 85%;">

### Neumannovy okrajové podmínky
Zadání tohoto typu okrajové podmínky implementujeme pomocí 2D pole `NBC`. Každý řádek tohoto pole obsahuje čtyři údaje:
1. `elementID`: číslo elementu
2. `edgeID`: lokální číslo hrany, na kterou se trakce aplikuje (1, 2, 3, nebo 4)
3. `tx`: x-ová složka trakčního vektoru v globálním souřadicovém systému
4. `ty`: y-ová složka trakčního vektoru v globálním souřadicovém systému

</td>
</tr></table>

In [6]:
A = 0.1; % m^2 cross section Area
thickness = sqrt(A); % thickness
NBC = [3 2 0.0 -1000/A]; % elementID = 3, edgeID = 2, tx = 0, t_y = -0.1 Pa

<table><tr>
<td style="width: 20%;">
    
![](assets/2D_quad_element_ISN.svg)

</td>
<td style="width: 80%;">

Pro aplikaci Neumanovy okrajové podmínky potřebujeme určit, na kterou hranu elementu ji aplikujeme. Za tímto účelem zavádíme pole konektivity `ISN` mezi lokálními čísly hran elementu (sloupce) a lokálními čísly uzlů (řádky), které tyto hrany definují. 

Používáme ho tak, že si z pole `IEN` nejprve "vyřízneme" globální čísla uzlů elementu `elementID`, ze kerých následně vyřízneme podmnožinu odpovídající hraně (segmentu) `edgeID` takto:
```octave
    nodes = IEN( ISN(:, edgeID), elementID);
```

</td>
</tr></table>

In [7]:
ISN = [2 3 4 1
       1 2 3 4];

## 3. Sestavení globání matice a vektoru

Na nejvyšší úrovni se provádí proces sestavení $\Aop_{el=1}^{n_\text{en}}$ globální matice tuhosti $\mathbf{K}$ a globálního vektoru pravé strany $\mathbf{f}$ z lokálních matic $\mathbf{K}_{el}$ a lokálních vektorů $\mathbf{f}_{el}$.

Nejprve si zvolíme, že neznámé složky posunutí pro jednotlivé uzly sítě budeme řadit ve vektoru řešní $\mathbf{u}$ takto:

$$
\begin{array}{c|ccccccccc}
i & 1 & 2 & 3 & 4 & 5 & 6 & \cdots & (n_{\text{np}}\times n_{\text{nd}})-1 & n_{\text{np}}\times n_{\text{nd}}\\
\hline
u_i & u_{1} & v_{1} & u_{2} & v_{2} & u_{3} & v_{3} & \cdots & u_{\text{nnp}} & v_{\text{nnp}}
\end{array}
$$

Vidíme, že délka vektoru $\mathbf{u}$ je součin počtu uzlů sítě `nnp` a počtu stupňů volnosti uzlu `nnd`, který je pro náš 2D případ roven 2.

Abychom se mohli snadněji odkazovat mezi globálními čísli uzlů $A\in\left[1,\ldots n_{\text{np}}\right]$ a čísly rovnic jim odpovídajícími $eq\in\left[1,\ldots n_{\text{eq}}\right]$, kde  $n_{\text{eq}}=n_{\text{np}}\times n_{\text{nd}}$, zavedeme další pomocné pole konektivity `ID` takto: 
$$
\mathtt{ID} = \left[\begin{array}{ccccc}
1 & 3 & 5 & \cdots & n_{\text{eq}} - 1 \\
2 & 4 & 6 & \ldots & n_{\text{eq}}
\end{array}\right]
$$
`A`-tý sloupec pole `ID` odpovídá `A`-tému globálnímu uzlu. Řádky v tomto `A`-tém sloupci obsahují odpovídající čísla neznámých složek vektoru posunutí $\mathbf{u}$.

Pole `ID` bychom mohli implementovat pomocí cyklu a indexové aritmetiky. Pro jednoduchost však využijeme vestavěné funkci `reshape()`, která 1D pole čísel rovnic převede na 2D pole, přesně jak jsme si definovali:

In [8]:
nnp = size(X, 2);  % Number of Nodal Points
nnd = nsd;         % Number of Nodal DOFs =nsd=2(ux, uy)
neq = nnp * nnd;   % Number od EQuations
ID = reshape(1:nnp*nnd, nnd, [])





ID =
    1    3    5    7    9   11   13   15
    2    4    6    8   10   12   14   16



Následující fragment kódu ukazuje proces sestavení jako cyklus přes všechny elementy `nel`, ve kterém se z pole konektivity `IEN` získají globální čísla úzlů `A` elementu `el`. Pro ty se následně z pole `ID` získají čísla rovnic `eq`. Protože `ID` je dvourozměrné pole, `eq` je také dvourozměrné. Abychom jej mohli použít jako řez globální maticí a vektorem, použijeme opět funkci `reshape()` a převedeme jej na jednorozměrný vektor indexů. V závěru for cyklu už jen snadno **kumulujeme** příspěvky z lokální matice.

In [9]:
K = sparse(neq, neq);

nel = size(IEN, 2); % Number of ELement
for el = 1:nel    

    A = IEN(:, el);

    Ke = zeros(nen*nnd, nen*nnd);

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    K(eq, eq) = K(eq, eq) + Ke;
end

Podobně postupujeme při sestavování vektoru pravé strany `f`. Neprovádíme však cyklus přes všechny elementy sítě, ale pouze přes řádky pole `NBC`, které odpovídají zatíženým hranám elementů. Z každého řádku pole `NBC` si nejprve načteme číslo elementu, lokální číslo hrany a složky trakčního vektoru. Po inicializaci lokálního vektoru `fe` již následujeme stejný proces sestavení globálního vektoru pravé strany `f` jako jsme provedli pro matici `K`.

In [10]:
nsn = size(ISN, 1); % Number of Segments Node
f = zeros(neq, 1);

for i = 1:size(NBC, 1)
    el = NBC(i, 1);
    edgeID = NBC(i, 2);
    tx = NBC(i, 3);
    ty = NBC(i ,4);

    A = IEN(ISN(:, edgeID), el);
    
    fe = zeros(nsn*nnd, 1);

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    f(eq) = f(eq) + fe;
end

## 4. Gaussova inetgrace

Pro výpočet lokální matice tuhosti $\mathbf{K}_{el}$ potřebujeme numerickou integraci přes objem elementu. Numerická integrace spočívá v aproximaci integrálu funkce sumací jejich funkčních hodnot ve vhodně vybraných bodech vynásobených váhovými koeficienty těchto bodů

$$
\int_{\square}f(\boldsymbol{\xi})\,\text{d}\boldsymbol{\xi}\approx\sum_{g=1}^{n_{\text{gp}}}f(\boldsymbol{\xi}_{g})w_{g}
$$

kde $\square\equiv\left[-1,1\right]\times\left[-1,1\right]$. Přechod od integrační oblasti $\square$ k oblasti elementu $\Omega_{el}$ souvisí s transformací isoparametrických souřadnic $\boldsymbol{\xi}$ na fyzikální souřadnice $\boldsymbol{x}$ a pozornost mu bude věnována později.

Konkrétní polohy integračních bodů a jejich váhy závisí na typu a řádu integrace. V MKP se nejčastěji používá Gaussova-Legendreova integrace. Je přesná pro polynomy až do stupně $2n-1$, kde $n$ je počet uzlů 1D integrace. Konkrétní definice poloh a vah integračních bodů nalezneme v literatuře, na [internetu](https://dlmf.nist.gov/3.5#v), nebo můžeme opět využít jazykové modely.

<div class="llm-prompt">
<strong>LLM Prompt:</strong> Dej mi dvě řádkové matice `gp` a `gw`, zapsané v syntaxi GNU Octave, jejichž sloupce budou odpovídat souřadnicím a vahám 2D Gaussovy- Legendreovy integrace řádu optimálního pro čtyřuzlové izoparametrické bilineární quad elementy.
</div>


In [11]:
gp_bulk = [-1 1 1 -1;
           -1 -1 1 1] / sqrt(3);
gw_bulk = [1 1 1 1];
ngp_bulk = length(gw_bulk);

Zbývá zanořit cyklus přes integrační body do cyklu přes elementy. V těchto bodech potřebujeme vyčíslit tvarové funkce a jejich derivace. Jak na to si ukážeme dále.

In [12]:
K = sparse(neq, neq);

nel = size(IEN, 2); % Number of ELement
for el = 1:nel
    A = IEN(:, el);

    Ke = zeros(nen*nnd, nen*nnd);
    for g = 1:ngp_bulk
       Xi = gp_bulk(:,g);
       w  = gw_bulk(g);
    end

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    K(eq, eq) = K(eq, eq) + Ke;
end

Vektor pravé strany obsahuje rovněž integrál. Nikoliv však přes obsah elementu, ale přes jeho okraj. Konkrétně hrana čtyřuzlového bilineárního quad elementu je dvouuzlový lineární line element. Potřebujeme tedy 1D integraci lineární funkce. Opět konkrétní polohy a váhy intehračních bodů najdeme buď v literatuře, nebo si o ně řekneme jazykovému modelu:

<div class="llm-prompt">
<strong>LLM Prompt:</strong> Dej mi dvě řádkové matice `gp` a `gw`, zapsané v syntaxi GNU Octave, jejichž sloupce budou odpovídat souřadnicím a vahám 1D Gaussovy- Legendreovy integrace řádu optimálního pro dvouuzlové izoparametrické lineární line elementy.
</div>

In [13]:
gp_boundary = [0];
gw_boundary = [2];
ngp_boundary = length(gw_boundary);

I v případě vektoru pravé strany zanoříme cyklus přes integrační body hraničního elementu:

In [14]:
f = zeros(neq, 1);

for i = 1:size(NBC, 1)
    el = NBC(i, 1);
    edgeID = NBC(i, 2);
    tx = NBC(i, 3);
    ty = NBC(i, 4);

    A = IEN(ISN(:, edgeID), el);

    fe = zeros(nsn*nnd, 1);
    for g = 1:ngp_boundary
       Xi = gp_boundary(:, g);
       w  = gw_boundary(g);
    end

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    f(eq) = f(eq) + fe;
end

## 5. Matice tvarových funkcí $\mathbf{N}$

O tvarové funkce quad elementu požádáme jazykový model:

<div class="llm-prompt">
<strong>LLM Prompt:</strong> Dej mi funkce v jazyku GNU Octave `bulkShapeFunctions(Xi)` a `bulkShapeFunctionsDerivatives(Xi)`, které pro zadané isoparametrické souřadnice Xi(1) a Xi(2) vrátí řádkové matice funkčních hodnot tvarových funkcí a jejich derivace pro isoparametrický bilineární čtyřuzlový quad element. Lokální číslování zvol v protisměru hodinových ručiček s počátkem v levém dolním rohu.
</div>

In [15]:
function N = bulkShapeFunctions(Xi)
    N = (1 + [-1 1 1 -1]*Xi(1)) .* (1 + [-1 -1 1 1]*Xi(2)) / 4;
end

function dNdXi = bulkShapeFunctionsDerivatives(Xi)
    dNdXi = [[-1 1 1 -1]   .* (1 + [-1 -1 1 1]*Xi(2));
        (1 + [-1 1 1 -1]*Xi(1)) .* [-1 -1 1 1]] / 4;
end

In [16]:
K = sparse(neq, neq);

nel = size(IEN, 2); % Number of ELement
for el = 1:nel

    A = IEN(:,el);

    Ke = zeros(nen*nnd, nen*nnd);
    for g = 1:ngp_bulk
       Xi = gp_bulk(:, g);
       w = gw_bulk(g);
       N = bulkShapeFunctions(Xi);
       dNdXi = bulkShapeFunctionsDerivatives(Xi);
    end

    eq = ID(:,A);
    eq = reshape(eq, [], 1);
    K(eq, eq) = K(eq, eq) + Ke;
end

O tvarové funkce line elementu potřebné k vyčíslení vektoru pravé strany opět požádáme LLM:

<div class="llm-prompt">
<strong>LLM Prompt:</strong> Dej mi funkce v jazyku GNU Octave `boundaryShapeFunctions(Xi)` a `boundaryShapeFunctionsDerivatives(Xi)`, které pro zadanou isoparametrickou souřadnici Xi(1) vrátí řádkové matice funkčních hodnot tvarových funkcí a jejich derivace pro isoparametrický lineární douuzlový line element. Počátek lokálního číslování zvol v levém bodě.
</div>


In [17]:
function N = boundaryShapeFunctions(Xi)
    N = [(1 - Xi(1)) / 2, (1 + Xi(1)) / 2];
end

function dN = boundaryShapeFunctionsDerivatives(Xi)
    dN = [-1/2, 1/2];
end

In [18]:
f = zeros(neq, 1);

for i = 1:size(NBC, 1)
    el = NBC(i, 1);
    edgeID = NBC(i, 2);
    tx = NBC(i, 3);
    ty = NBC(i, 4);

    A = IEN(ISN(:, edgeID), el);

    fe = zeros(nsn*nnd, 1);
    for g = 1:ngp_boundary
       Xi = gp_boundary(:, g);
       w  = gw_boundary(g);
       N = boundaryShapeFunctions(Xi);
       dNdXi = boundaryShapeFunctionsDerivatives(Xi);
    end
    
    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    f(eq) = f(eq) + fe;
end

## 6. Operátorová matice $\mathbf{B}$

Operátorová matice $\mathbf{B}$ zobrazuje vektor posunutí $\mathbf{u}$ na vektor přetvoření $\left\{ \boldsymbol{\varepsilon}\right\} $:
$$
\left\{ \boldsymbol{\varepsilon}\right\} =\mathbf{B}\mathbf{u}
$$
Pro 2D případ je definována jako:
$$
\left\{ \begin{array}{c}
\varepsilon_{x}\\
\varepsilon_{y}\\
\gamma_{xy}
\end{array}\right\} =\left[\begin{array}{cc}
\frac{\partial}{\partial x} & 0\\
0 & \frac{\partial}{\partial y}\\
\frac{\partial}{\partial y} & \frac{\partial}{\partial x}
\end{array}\right]\left\{ \begin{array}{c}
u\\
v
\end{array}\right\} =\left[\begin{array}{cc}
\frac{\partial}{\partial x} & 0\\
0 & \frac{\partial}{\partial y}\\
\frac{\partial}{\partial y} & \frac{\partial}{\partial x}
\end{array}\right]\left\{ \begin{array}{c}
\sum_{a=1}^{n_{\text{en}}}N_{a}u_{a}\\
\sum_{a=1}^{n_{\text{en}}}N_{a}v_{a}
\end{array}\right\} 
$$
$$
\left\{ \begin{array}{c}
\varepsilon_{x}\\
\varepsilon_{y}\\
\gamma_{xy}
\end{array}\right\} =\left[\left[\begin{array}{cc}
\frac{\partial N_{1}}{\partial x} & 0\\
0 & \frac{\partial N_{1}}{\partial y}\\
\frac{\partial N_{1}}{\partial y} & \frac{\partial N_{1}}{\partial x}
\end{array}\right]\cdots\left[\begin{array}{cc}
\frac{\partial N_{n_{\text{en}}}}{\partial x} & 0\\
0 & \frac{\partial N_{n_{\text{en}}}}{\partial y}\\
\frac{\partial N_{n_{\text{en}}}}{\partial y} & \frac{\partial N_{n_{\text{en}}}}{\partial x}
\end{array}\right]\right]\left\{ \begin{array}{c}
u_{a}\\
v_{a}\\
\vdots\\
u_{n_{\text{en}}}\\
v_{n_{\text{en}}}
\end{array}\right\} 
$$

Následující funkce implementuje tvorbu operátorové matice `B`. Všimněte si, že parametrem této funkce jsou derivace tvarových funkcí podle fyzikálních souřadnic $\boldsymbol{x}$. K dispozici však máme v tuto chvíli pouze derivace podle isoparametrických souřadnic $\boldsymbol{\xi}$. Potřebujeme proto transformovat suřadnice, viz dále.

In [19]:
function B = createMatrixB(dNdX)
    nsd = size(dNdX, 1); % Number of Spatial Dimensions
    nen = size(dNdX, 2); % Number of Element Nodes
    B = zeros(nsd+1, nsd*nen);
    for a = 1:nen
        B(:, (a-1)*nsd+1:a*nsd ) = [
         dNdX(1, a)     0
            0        dNdX(2, a)
         dNdX(2, a)  dNdX(1, a)];
    end
end

Princip isoparametrických elementů spočívá v tom, že stejná diskretizace, která je použita pro neznámé pole je použita k popisu fyzikálních souřadnic:
$$
\boldsymbol{u}(\boldsymbol{\xi})=\sum_{a=1}^{n_{\text{en}}}N_{a}(\boldsymbol{\xi})\boldsymbol{u}_{a},\qquad\boldsymbol{x}(\boldsymbol{\xi})=\sum_{a=1}^{n_{\text{en}}}N_{a}(\boldsymbol{\xi})\boldsymbol{x}_{a}
$$
Pro diferenciál fyzikálních sořadnic platí:
$$
\text{d}\boldsymbol{x}=\frac{\partial\boldsymbol{x}}{\partial\boldsymbol{\xi}}\text{d}\boldsymbol{\xi}=\mathbf{J}\text{d}\boldsymbol{\xi}
$$
kde $\mathbf{J}$ se nazývá Jacobiho matice, kterou můžeme pomocí tvarových funkcí a uzlových fyzikálních souřadnic zapsat jako:
$$
\mathbf{J}=\left[\begin{array}{ccc}
x_{1} & \cdots & x_{n_{\text{en}}}\\
y_{1} & \cdots & y_{n_{\text{en}}}
\end{array}\right]\left[\begin{array}{cc}
\frac{\partial N_{1}}{\partial\xi_{1}} & \frac{\partial N_{1}}{\partial\xi_{2}}\\
\vdots & \vdots\\
\frac{\partial N_{n_{\text{en}}}}{\partial\xi_{1}} & \frac{\partial N_{n_{\text{en}}}}{\partial\xi_{2}}
\end{array}\right]
$$

Derivace tvarových funkcí podle fyzikálních souřadnic získáme pravidlem pro derivování složené funkce:
$$
\frac{\partial\mathbf{N}(\boldsymbol{\xi}(\boldsymbol{x}))}{\partial\boldsymbol{x}}=\frac{\partial\mathbf{N}}{\partial\boldsymbol{\xi}}^{\mathsf{T}}\frac{\partial\boldsymbol{\xi}}{\partial\boldsymbol{x}}=\frac{\partial\mathbf{N}}{\partial\boldsymbol{\xi}}^{\mathsf{T}}\left[\frac{\partial\boldsymbol{x}}{\partial\boldsymbol{\xi}}\right]^{-1}=\mathbf{J}^{-\mathsf{T}}\frac{\partial\mathbf{N}}{\partial\boldsymbol{\xi}}
$$
a zapsáno ve složkách pro všech `nen` složek:
$$
\left[\begin{array}{c}
\frac{\partial N_{1}}{\partial x}\\
\frac{\partial N_{1}}{\partial y}
\end{array}\cdots\begin{array}{c}
\frac{\partial N_{n_{\text{en}}}}{\partial x}\\
\frac{\partial N_{n_{\text{en}}}}{\partial y}
\end{array}\right]=\left[\begin{array}{cc}
\frac{\partial x}{\partial\xi_{1}} & \frac{\partial x}{\partial\xi_{2}}\\
\frac{\partial y}{\partial\xi_{1}} & \frac{\partial y}{\partial\xi_{2}}
\end{array}\right]^{-\mathsf{T}}\left[\begin{array}{c}
\frac{\partial N_{1}}{\partial\xi_{1}}\\
\frac{\partial N_{1}}{\partial\xi_{2}}
\end{array}\cdots\begin{array}{c}
\frac{\partial N_{n_{\text{en}}}}{\partial\xi_{1}}\\
\frac{\partial N_{n_{\text{en}}}}{\partial\xi_{2}}
\end{array}\right]
$$

Pro diferenciál quad elementu ve 2D můžeme psát:
$$
\text{d}\Omega_{el}=\left\Vert \frac{\partial\boldsymbol{x}}{\partial\xi_{1}}\text{d}\xi_{1}\times\frac{\partial\boldsymbol{x}}{\partial\xi_{2}}\text{d}\xi_{2}\right\Vert =\left\Vert \frac{\partial\boldsymbol{x}}{\partial\xi_{1}}\times\frac{\partial\boldsymbol{x}}{\partial\xi_{2}}\right\Vert \text{d}\xi_{1}\text{d}\xi_{2}=\det(\mathbf{J})\text{d}\xi_{1}\text{d}\xi_{2}
$$

In [20]:
K = sparse(neq, neq);

nel = size(IEN, 2); % Number of ELement
for el = 1:nel

    A = IEN(:, el);
    Xe = X(:, A);

    Ke = zeros(nen*nnd, nen*nnd);
    for g = 1:ngp_bulk
        Xi = gp_bulk(:, g);
        w  = gw_bulk(g);
        N = bulkShapeFunctions(Xi);
        dNdXi = bulkShapeFunctionsDerivatives(Xi);
       
        
        Je = Xe * dNdXi';
        je = det(Je);
        dNdX = inv(Je)' * dNdXi;
        Be = createMatrixB(dNdX);
    end

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    K(eq, eq) = K(eq, eq) + Ke;
end

`Line` element ve 2D je tzv. varieta. To znamená, že jeho dvě fyzikální složky souřadnice $x, y$ jsou parametrizovány pouze jednou isoparametrickou souřadnicí $\xi$. Důsledkem je, že Jacobiho matice není čtvercová matice. V konkrétním případě `Line` element ve 2D je Jacobiho matice vektor, jehož délka je jacobián transformace.
$$
\text{d}\boldsymbol{x}=\frac{\text{d}\boldsymbol{x}}{\text{d}\xi}\text{d}\xi=\boldsymbol{J}\text{d}\xi,\qquad\left\{ \begin{array}{c}
\text{d}x\\
\text{d}y
\end{array}\right\} =\left[\begin{array}{c}
\frac{\text{d}x}{\text{d}\xi}\\
\frac{\text{d}y}{\text{d}\xi}
\end{array}\right]\text{d}\xi
$$
Pro diferenciál `line` elementu ve 2D můžeme psát:
$$
\text{d}\Gamma_{\text{N}}=\left\Vert \frac{\text{d}\boldsymbol{x}}{\text{d}\xi}\right\Vert \text{d}\xi
$$

In [21]:
f = zeros(neq, 1);

for i = 1:size(NBC, 1)
    el = NBC(i, 1);
    edgeID = NBC(i, 2);
    tx = NBC(i, 3);
    ty = NBC(i, 4);

    A = IEN(ISN(:, edgeID), el);
    Xe = X(:, A);
    
    fe = zeros(nsn*nnd, 1);
    for g = 1:ngp_boundary
       Xi = gp_boundary(:, g);
       w  = gw_boundary(g);
       N = boundaryShapeFunctions(Xi);
       dNdXi = boundaryShapeFunctionsDerivatives(Xi);
   
       Je = Xe * dNdXi';
       je = norm(Je);
       fe = fe + kron(N', [tx; ty]) * w * je * thickness;
    end

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    f(eq) = f(eq) + fe;
end

## 6. Matice materiálové tuhosti $\mathbf{D}$

Matice materiálové tuhosti je lineární operátor, který vektor přetvoření $\left\{ \boldsymbol{\varepsilon}\right\}$ zobrazí na vektor napětí $\left\{ \boldsymbol{\sigma}\right\}$: 
$$
\left\{ \boldsymbol{\sigma}\right\} =\mathbf{D}\left\{ \boldsymbol{\varepsilon}\right\} 
$$
podobně jako to dělá konstanta úměrnosti (Youngův modul pružnosti) $E$ v 1D podobě Hookeova zákona: 
$$
\sigma=E\varepsilon
$$
Ve 2D je potřeba rozlišovat mezi případem rovinné **deformace** a rovinné **napjatosti** viz poznámky nebo následující prompt pro LLM.

<div class="llm-prompt">
<strong>LLM Prompt:</strong> Dej mi matici materiálové tuhosti D pro případ rovinné deformace zapsanou v syntaxi GNU Octave.
</div>

In [22]:
E = 2.1e11;   % (Pa) Youngův modul
nu = 0.3;    % (-) Poissonovo číslo
D = E / ((1 + nu) * (1 - 2*nu)) * [1-nu,  nu,       0;
                                   nu,    1-nu,     0;
                                   0,     0,    (1-2*nu)/2];

In [23]:
K = sparse(neq, neq);

nel = size(IEN, 2); % Number of ELement
for el = 1:nel

    A = IEN(:, el);
    Xe = X(:, A);
    
    Ke = zeros(nen*nnd, nen*nnd);
    for g = 1:ngp_bulk
        Xi = gp_bulk(:, g);
        w  = gw_bulk(g);
        N = bulkShapeFunctions(Xi);
        dNdXi = bulkShapeFunctionsDerivatives(Xi);
       
        Je = Xe * dNdXi';
        j = det(Je);
        dNdX = inv(Je)' * dNdXi;
        Be = createMatrixB(dNdX);
        
        Ke = Ke + Be'*D*Be * w * j * thickness;
    end

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    K(eq, eq) = K(eq, eq) + Ke;
end

In [24]:
f = zeros(neq, 1);

for i = 1:size(NBC, 1)
    el = NBC(i, 1);
    sg = NBC(i, 2);
    tx = NBC(i, 3);
    ty = NBC(i, 4);
    
    A = IEN(ISN(:, sg), el);
    Xe = X(:, A);
            
    fe = zeros(nsn*nnd, 1);    
    for g = 1:ngp_boundary
        Xi = gp_boundary(:, g);
        w  = gw_boundary(g);
        N = boundaryShapeFunctions(Xi);
        dNdXi = boundaryShapeFunctionsDerivatives(Xi);
       
        Je = Xe * dNdXi';
        je = norm(Je);

        fe = fe + kron(N', [tx; ty]) * w * je * thickness;
    end

    eq = ID(:, A);
    eq = reshape(eq, [], 1);
    f(eq) = f(eq) + fe;
end

## 8. Řešení
Zatímco Neumannovy okrajové podmínky jsme aplikovali při integraci vektoru pravé strany `f`, Dirichletovy okrajové podmínky jsme zatím nezohlednili. *Homogenní* Dirichletovy okrajové podmínky vynutíme tak, že řádek matice `K` a vektoru pravé strany `f` odpovídající předepsanému stupni volnosti vynulujeme, stejně jako sloupec matice `K`, a diagonální hodnotu změníme na 1.

Elegantní způsob jak vynutit *nehomogenní* Dirichletovy okrajové podmínky je použít Newtonovu-Raphsonovu (NR) metodu pro řešení nelineární soustavy rovnic. Protože náš problém je lineární, k dosažení řešení nám bude stačit jedna iterace. Myšlenka NR metody spočíví v linearizaci reziduál
$$
\mathbf{r}(\mathbf{u}+\Delta\mathbf{u})\approx\mathbf{r}(\mathbf{u})+\frac{\partial\mathbf{r}(\mathbf{u})}{\partial\mathbf{u}}\Delta\mathbf{u}=\mathbf{0}
$$
a následné aktualizaci přírůstků řešení
$$
\mathbf{u}_{k+1}=\mathbf{u}_{k}+\Delta\mathbf{u}_{k}
$$
dokud není přírůstek $\Delta\mathbf{u}$ resp. residuál $\mathbf{r}(\mathbf{u})$ dostatečně malý.

V našem případě má residuál tvar:
$$
\mathbf{r}(\mathbf{u})=\mathbf{K}\mathbf{u}-\mathbf{f}=\mathbf{0}
$$
a jeho derivace podle $\mathbf{u}$:
$$
\frac{\partial\mathbf{r}(\mathbf{u})}{\partial\mathbf{u}}=\mathbf{K}
$$
Z linearizace pak plyne:
$$
\mathbf{K}\Delta\mathbf{u}=-\mathbf{r}
$$
Řešení nalezneme způsobem, že počáteční odhad řešení $\mathbf{u}_{0}$ zvolíme tak, aby předepsané stupně volnosti splňovaly Dirichletovy okrajové podmínky:

In [25]:
for i = 1:size(DBC, 1)
    nodeID = DBC(i, 1);
    dofID  = DBC(i, 2); 
    eq = ID(dofID, nodeID);
    f(eq) = 0.0;
    K(:, eq) = 0.0;
    K(eq, :) = 0.0;
    K(eq, eq) = 1.0;
end

Soustavu lineárních algebraických rovnic
$$
\mathbf{u}=\mathbf{K}^{-1}\mathbf{f}
$$
v GNU Octave vyřešíme operátorem zpětné lomítko:

In [26]:
u = K \ f;

fprintf("Maximal displacement is %g (m).\n", max(abs(full(u))));




Maximal displacement is 4.33333e-08 (m).


a jim odpovídající elementy vektoru přírůstků $\Delta\mathbf{u}$ po vyřešení položíme rovny nule a aktualizujeme počáteční odhad:

In [27]:
%u = zeros(neq, 1);
%u(ceq) = DBC(:,3); % asign prescribed values

%r = K*u - f;
%r(ceq) = 0.0;
%du = K \ -r; % solving algebaic linear system
%u = u + du;
%u

## 9. Post-processing

In [28]:
function plotDisplacement(X, IEN, u, nsd, nel, max_U_scale)
    U = reshape(u, nsd, []);
    scale = 1/max(abs(u)) * max_U_scale;
    x = X + scale*U;
    figure(1); clf; set(gcf, 'position', [100, 100, 800, 600]);

    for e = 1:nel
        xe = [x(1,IEN(1,e)) x(1,IEN(2,e)); x(1,IEN(4,e)) x(1,IEN(3,e))];
        ye = [x(2,IEN(1,e)) x(2,IEN(2,e)); x(2,IEN(4,e)) x(2,IEN(3,e))];
        ze = [0 0; 0 0];
        ue = [U(2,IEN(1,e)) U(2,IEN(2,e)); U(2,IEN(4,e)) U(2,IEN(3,e))];
        surf(xe,ye,ue); hold on;
        plot([X(1,IEN(:,e)) X(1,IEN(1,e))], [X(2,IEN(:,e)) X(2,IEN(1,e))],'k--');
        hold on;
        plot([x(1,IEN(:,e)) x(1,IEN(1,e))], [x(2,IEN(:,e)) x(2,IEN(1,e))],'k-');
    end
    cm = colormap("viridis"); colormap(1 - cm);
    view(0,90); h = colorbar; shading interp;
    ylabel(h, "y-displacement (m)");
    xlabel('x (m)'); ylabel('y (m)');
    axis equal; grid on; box on;
end

In [29]:
plotDisplacement(X, IEN, u, nsd, nel, 0.2);